In [1]:
using DifferentialEquations # : ODEProblem, solve
using DataFrames: DataFrame
using CSV: File as CSVFile

In [2]:
using Plots
using BenchmarkTools

In [3]:
dirname_model = "../src/model_ctypes/ina_pipette/"

filename_legend_constants = Base.Filesystem.joinpath(dirname_model, "legend_constants_v2.csv")
filename_legend_states = Base.Filesystem.joinpath(dirname_model, "legend_states.csv")
filename_protocol = Base.Filesystem.joinpath("../data/protocols/protocol_sparse.csv");

In [4]:
legend_states = DataFrame(CSVFile(filename_legend_states))
legend_constants = DataFrame(CSVFile(filename_legend_constants))
protocol = DataFrame(CSVFile(filename_protocol));

In [5]:
function find_step(t, protocol)
    index = findfirst(x -> x >= t, protocol.t)
    v = protocol.v[index]
end

find_step (generic function with 1 method)

# Define model

In [6]:
function compute_algebraic(du, u, p, t)
    
    v_comp, v_p, v_m, m, h, j, I_out = u
    
    v_c = p.v_c  # find_step(t)
    
    tau_m = 1 / (p.a0_m * exp(v_m / p.s_m) + p.b0_m * exp(-v_m / p.delta_m))
    tau_h = 1 / (p.a0_h * exp(-v_m / p.s_h) + p.b0_h * exp(v_m / p.delta_h))
    tau_j = p.tau_j_const + 1 / (p.a0_j * exp(-v_m / p.s_j) + p.b0_j * exp(v_m / p.delta_j))
    
    m_inf = 1 / (1 + exp(-(p.v_half_m + v_m) / p.k_m))
    h_inf = 1 / (1 + exp((p.v_half_h + v_m) / p.k_h))
    
    v_cp = v_c + (v_c - v_comp) * (1 / (1 - p.alpha) - 1)

    I_leak = p.g_leak * v_m
    I_Na = p.g_max * h * m^3 * j * (v_m - p.v_rev)
    I_c = 1e9 * p.c_m * ((v_p + p.v_off - v_m) / (p.R * p.c_m) - 1e-9 * (I_leak + I_Na) / p.c_m)
    I_p = 1e9 * p.c_p * (v_cp - v_p) / (p.c_p * p.R_f)
    I_comp = 1e9 * p.x_c_comp * p.c_m * (v_c - v_comp) / (p.x_c_comp * p.c_m * p.x_r_comp * p.R * (1 - p.alpha))
    I_in = I_leak + I_Na + I_c  + I_p - I_comp
    
    a = (tau_m=tau_m, tau_h=tau_h, tau_j=tau_j,
         m_inf=m_inf, h_inf=h_inf,
         v_cp=v_cp, I_leak=I_leak, I_Na=I_Na, I_c=I_c, I_p=I_p, I_comp=I_comp, I_in=I_in,
         v_c=v_c)
    
    return a
end

compute_algebraic (generic function with 1 method)

In [7]:
function compute_rates!(du, u, p, t)
        
    v_comp, v_p, v_m, m, h, j, I_out = u
    a = compute_algebraic(du, u, p, t)
    
    du[1] = (a.v_c - v_comp) / (p.x_c_comp * p.c_m * p.x_r_comp * p.R * (1 - p.alpha))  # v_comp
    du[2] = (a.v_cp - v_p) / (p.c_p * p.R_f)  # v_p
    du[3] = (v_p + p.v_off - v_m) / (p.R * p.c_m) - (1e-9) * (a.I_leak + a.I_Na) / p.c_m  # v_m
        
    du[4] = (a.m_inf - m) / a.tau_m  # m
    du[5] = (a.h_inf - h) / a.tau_h  # h
    du[6] = (a.h_inf - j) / a.tau_j  # j
        
    du[7] = (a.I_in - I_out) / p.tau_z  # I_out
    
    nothing
end

compute_rates! (generic function with 1 method)

In [8]:
function create_p_from_legend(legend)
    p = collect(zip(Symbol.(legend[!, :name]), legend[!, :value]))
    p = NamedTuple(p)
end

create_p_from_legend (generic function with 1 method)

# Callbacks

In [9]:
function affect!(integrator)
    t = integrator.t
    v_c = find_step(t, protocol)
    p = integrator.p
    k, v = keys(p), collect(values(p))
    v[end] = v_c
    p = NamedTuple(collect(zip(k, v)))
    integrator.p = p
    set_proposed_dt!(integrator, 1e-9)
    nothing
end

cb = PresetTimeCallback(protocol.t, affect!);

In [10]:
# func = ODEFunction(compute_rates!, syms=[:v_comp, :v_p, :v_m, :m, :h, :j, :I_out])
func = ODEFunction(compute_rates!, syms=[:I_out])

(::ODEFunction{true, typeof(compute_rates!), LinearAlgebra.UniformScaling{Bool}, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Nothing, Vector{Symbol}, Nothing, typeof(SciMLBase.DEFAULT_OBSERVED), Nothing}) (generic function with 7 methods)

In [11]:
u₀ = [-80.0, -80.0, -80.0, 0.0, 1.0, 1.0, 0.0]
tspan = (0., 5.)
p = create_p_from_legend(legend_constants)

prob = ODEProblem(func, u₀, tspan, p,
                  callback=cb);

In [12]:
saveat = 0: 5e-5: 5
reltol = 1e-3
abstol = 1e-3

sol = solve(prob, alg=Rodas4(), reltol=reltol, abstol=abstol, saveat=saveat, save_idxs=[7]);

In [13]:
@benchmark solve(prob, alg=Rodas4(), reltol=reltol, abstol=abstol, saveat=saveat, save_idxs=[7])

BenchmarkTools.Trial: 
  memory estimate:  26.86 MiB
  allocs estimate:  213382
  --------------
  minimum time:     43.709 ms (0.00% GC)
  median time:      45.476 ms (0.00% GC)
  mean time:        50.504 ms (6.13% GC)
  maximum time:     106.895 ms (20.23% GC)
  --------------
  samples:          100
  evals/sample:     1

# BlackBox

In [14]:
using BlackBoxOptim

In [15]:
data = deepcopy(vcat(sol.u...));

In [16]:
function loss(data, sol)
    u = vcat(sol.u...)
    return √(mean((data .- u).^2))
end

loss (generic function with 1 method)

In [17]:
loss(data, sol)

0.0

In [18]:
prob = ODEProblem(func, u₀, tspan, p,
                  callback=cb);

In [19]:
function calculate_solution(x)
    
    v_rev = 18.0
    v_c = -80.0
    
    p_vec = vcat(x, [v_rev, v_c])

    p = create_p_from_legend(legend_constants)
    p = collect(zip(keys(p), p_vec))
    p = NamedTuple(p)
    
    prob = ODEProblem(func, u₀, tspan, p, callback=cb)

    solver_kwargs = (reltol=reltol, abstol=abstol, saveat=saveat,
                     save_idxs=[7],
                     )

    sol = solve(prob, alg=Rodas5(); solver_kwargs...);
    
end

calculate_solution (generic function with 1 method)

In [20]:
function my_model(x)
    
    sol = calculate_solution(x)
    
    if length(sol) ≠ length(data)
        return Inf
    end
    
    loss(data, sol)
    
end

my_model (generic function with 1 method)

In [21]:
p_vec = collect(values(p))

30-element Vector{Float64}:
     4.502963e-12
     2.473016e-11
 16529.06
   386.7
    22.823
    12.8321
     6.26
 58131.407
    10.27583
    21.62
     0.6462
 11358.31
     7.445
     ⋮
     0.4812443
     0.000100034
    28.35802
    59.69117
     7.66677
     5.507771
     0.01
     0.2
     0.75
    -2.0
    18.0
   -80.0

In [22]:
bounds = collect(zip(legend_constants.bound_1, legend_constants.bound_2))[1: end-2];

In [23]:
res = bboptimize(my_model; SearchRange=bounds, MaxTime=60., PopulationSize=256)

Starting optimization with optimizer DiffEvoOpt{FitPopulation{Float64}, RadiusLimitedSelector, BlackBoxOptim.AdaptiveDiffEvoRandBin{3}, RandomBound{ContinuousRectSearchSpace}}
0.00 secs, 0 evals, 0 steps
0.59 secs, 6 evals, 3 steps, improv/step: 1.000 (last = 1.0000), fitness=140.985818963
1.11 secs, 12 evals, 6 steps, improv/step: 0.667 (last = 0.3333), fitness=88.005709546
1.66 secs, 20 evals, 10 steps

┌ Warning: Instability detected. Aborting
└ @ SciMLBase /home/andrey/.julia/packages/SciMLBase/UIp7W/src/integrator_interface.jl:351


, improv/step: 0.600 (last = 0.5000), fitness=88.005709546
2.27 secs, 28 evals, 14 steps, improv/step: 0.429 (last = 0.0000), fitness=88.005709546
2.81 secs, 36 evals, 18 steps, improv/step: 0.444 (last = 0.5000), fitness=88.005709546
3.36 secs, 44 evals, 22 steps, improv/step: 0.409 (last = 0.2500), fitness=82.754167918
3.96 secs, 54 evals, 28 steps, improv/step: 0.500 (last = 0.8333), fitness=82.754167918
4.59 secs, 64 evals, 33 steps, improv/step: 0.545 (last = 0.8000), fitness=81.603385868
5.09 secs, 72 evals, 37 steps, improv/step: 0.541 (last = 0.5000), fitness=81.603385868
5.64 secs, 81 evals, 42 steps, improv/step: 0.595 (last = 1.0000), fitness=81.603385868
6.23 secs, 91 evals, 47 steps, improv/step: 0.553 (last = 0.2000), fitness=81.603385868
6.85 secs, 101 evals, 52 steps, improv/step: 0.558 (last = 0.6000), fitness=81.603385868
7.46 secs, 111 evals, 57 steps, improv/step: 0.561 (last = 0.6000), fitness=81.603385868
8.14 secs, 121 evals, 62 steps, improv/step: 0.581 (last = 

┌ Warning: Instability detected. Aborting
└ @ SciMLBase /home/andrey/.julia/packages/SciMLBase/UIp7W/src/integrator_interface.jl:351


8.74 secs, 131 evals, 68 steps, improv/step: 0.544 (last = 0.1667), fitness=81.603385868
9.28 secs, 140 evals, 73 steps, improv/step: 0.548 (last = 0.6000), fitness=81.603385868
9.82 secs, 149 evals, 78 steps, improv/step: 0.564 (last = 0.8000), fitness=81.603385868
10.46 secs, 158 evals, 83 steps, improv/step: 0.542 (last = 0.2000), fitness=81.603385868
10.97 secs, 166 evals, 88 steps, improv/step: 0.534 (last = 0.4000), fitness=81.603385868


...

┌ Warning: Instability detected. Aborting
└ @ SciMLBase /home/andrey/.julia/packages/SciMLBase/UIp7W/src/integrator_interface.jl:351
┌ Warning: Instability detected. Aborting
└ @ SciMLBase /home/andrey/.julia/packages/SciMLBase/UIp7W/src/integrator_interface.jl:351


56.92 secs, 927 evals, 578 steps, improv/step: 0.471 (last = 0.7143), fitness=22.404718729
57.42 secs, 934 evals, 583 steps, improv/step: 0.470 (last = 0.4000), fitness=22.404718729


┌ Warning: Instability detected. Aborting
└ @ SciMLBase /home/andrey/.julia/packages/SciMLBase/UIp7W/src/integrator_interface.jl:351
┌ Warning: Instability detected. Aborting
└ @ SciMLBase /home/andrey/.julia/packages/SciMLBase/UIp7W/src/integrator_interface.jl:351


57.96 secs, 944 evals, 591 steps, improv/step: 0.467 (last = 0.2500), fitness=22.404718729
58.54 secs, 953 evals, 597 steps, improv/step: 0.466 (last = 0.3333), fitness=22.404718729
59.09 secs, 961 evals, 603 steps, improv/step: 0.466 (last = 0.5000), fitness=22.404718729
59.62 secs, 969 evals, 610 steps, improv/step: 0.466 (last = 0.4286), fitness=22.404718729

Optimization stopped after 615 steps and 60.07 seconds
Termination reason: Max time (60.0 s) reached
Steps per second = 10.24
Function evals per second = 16.25
Improvements/step = Inf
Total function evaluations = 976


Best candidate found: [4.92272e-12, 2.1749e-11, 85345.5, 656.564, 1.76218, 85.5557, 73.5813, 14895.9, 65.9213, 73.6602, 0.0980055, 59095.9, 79.8362, 32.2562, 0.00131669, 2.81751e7, 6.89964e5, 5433.86, 0.552367, 0.000165772, 32.5627, 74.7225, 7.44183, 9.88139, 0.01013, 0.189758, 0.768757, 11.226]

Fitness: 22.404718729



BlackBoxOptim.OptimizationResults("adaptive_de_rand_1_bin_radiuslimited", "Max time (60.0 s) reached", 615, 1.63061361611038e9, 60.07238698005676, ParamsDictChain[ParamsDictChain[Dict{Symbol, Any}(:RngSeed => 829861, :MaxTime => 60.0, :SearchRange => [(1.0e-14, 5.0e-12), (1.0e-11, 9.0e-11), (10000.0, 100000.0), (100.0, 1000.0), (1.0, 100.0), (1.0, 100.0), (1.0, 100.0), (10000.0, 100000.0), (1.0, 100.0), (1.0, 100.0)  …  (0.01, 1.0), (1.0e-5, 0.001), (10.0, 60.0), (50.0, 100.0), (1.0, 10.0), (1.0, 10.0), (0.01, 1.1), (0.01, 1.1), (0.7, 0.8), (-15.0, 15.0)], :MaxFuncEvals => 0, :MaxSteps => 0, :PopulationSize => 256),Dict{Symbol, Any}()],Dict{Symbol, Any}(:CallbackInterval => -1.0, :TargetFitness => nothing, :TraceMode => :compact, :FitnessScheme => ScalarFitnessScheme{true}(), :MinDeltaFitnessTolerance => 1.0e-50, :NumDimensions => :NotSpecified, :FitnessTolerance => 1.0e-8, :TraceInterval => 0.5, :MaxStepsWithoutProgress => 10000, :MaxSteps => 10000…)], 976, ScalarFitnessScheme{true}()

In [28]:
p_best = best_candidate(res);

In [29]:
sol_best = calculate_solution(p_best);

In [32]:
plot(sol_best)
plot!(sol_best.t, data)
plot!(xlim=(4.8, 4.9),
      # ylim=(-200, 100),
     )

In [31]:
plot(sol_best)
plot!(sol_best.t, data)

In [34]:
Dict(zip(keys(p), p_best))

Dict{Symbol, Float64} with 28 entries:
  :alpha       => 0.768757
  :x_c_comp    => 0.01013
  :k_m         => 7.44183
  :a0_j        => 0.0980055
  :c_m         => 2.1749e-11
  :x_r_comp    => 0.189758
  :g_max       => 5433.86
  :delta_j     => 79.8362
  :delta_h     => 65.9213
  :tau_z       => 0.000165772
  :b0_h        => 14895.9
  :v_half_h    => 74.7225
  :a0_m        => 85345.5
  :s_j         => 32.2562
  :delta_m     => 1.76218
  :R           => 2.81751e7
  :v_half_m    => 32.5627
  :s_m         => 85.5557
  :a0_h        => 73.5813
  :s_h         => 73.6602
  :R_f         => 6.89964e5
  :tau_j_const => 0.00131669
  :k_h         => 9.88139
  :v_off       => 11.226
  :b0_m        => 656.564
  ⋮            => ⋮

In [36]:
res.archive_output

BlackBoxOptim.TopListArchiveOutput{Float64, Vector{Float64}}(22.40471872850286, [4.922724085562701e-12, 2.1748983800032484e-11, 85345.52519790507, 656.5637254857447, 1.7621838287219138, 85.55571711137488, 73.5812780818534, 14895.917125934095, 65.92133287660124, 73.66019816830496  …  0.5523669447580015, 0.00016577198000179537, 32.562665232278796, 74.7225444883995, 7.44182605942426, 9.881388074748042, 0.010130049285124135, 0.1897577400146785, 0.7687567729796961, 11.226004108844055])